# Primeira etapa do desafio

1.	Realize a extração dos dados dos 3 ultimos meses de prescrição (english-prescribing-data-epd) sem contar o ultimo, fonte: https://opendata.nhsbsa.net/dataset/english-prescribing-data-epd

## Mês de Agosto
- Por se tratar de uma grande massa de dados, optei por fazer o processamento individualmente por mês em cada notebook.
- Tambem por esse motivo optei por fazer todo o armazemento e excução na minha maquina local, para evitar problemas de custos extras pelo volume de dados armazenados e processados

---

### Fazendo as importações dos frameworks/metodos necessarios para executar as funções do jupyter 

In [1]:
import pandas as pd
import pyspark.sql.functions as func

from pyspark.sql import SparkSession
from pyspark.sql.functions import *

import findspark
findspark.init()
findspark.find()
import pyspark
findspark.find()

'E:\\spark-3.3.1-bin-hadoop3'

In [2]:
from pyspark import SparkContext, SparkConf
from pyspark.sql import SparkSession
conf = pyspark.SparkConf().setAppName('appName').setMaster('local')
sc = pyspark.SparkContext(conf=conf)
spark = SparkSession(sc)

In [7]:
spark = SparkSession.builder.getOrCreate()

### Criando o DF principal:
- Aqui optei por deixar comentado a amostra da visualização dos dados no Spark, pois pelo tamanho massivo do DF, a representação não estava satisfatoria ao meu ver. Mais a baixo ultilizarei o pandas como alternativa.

In [8]:
df_spark = spark.read.csv(r'C:\Users\arthu\Desktop\EPD_202208.csv', sep = ',', inferSchema=True, header=True)
# df_spark.show(10)


### Conseguindo a importação pela API
- Alternativa de importação dos dados usando API, pois a fornecida pelo site não foi compativel para mim.


In [14]:
#import urllib.request

#url = 'https://opendata.nhsbsa.net/dataset/65050ec0-5abd-48ce-989d-defc08ed837e/resource/bc3cb910-f841-47e0-9fb6-203d141c57d6/download/epd_202208.csv'  
#fileobj = urllib.request.urlopen(url)

#for linha in fileobj:
#    print(linha)
#    break

### Obtendo as informações necessarias da importação realizada :
- Concluindo a validação dos dados extraídos

In [9]:
print("Total de linhas: ", df_spark.count(),"\n" # Conferindo se todas as linhas foram importadas por completo
      "Total de colunas: ", len(df_spark.columns)) # Numero de colunas
df_spark.printSchema() # Conferindo o nome das colunas para consulta

Total de linhas:  17621811 
Total de colunas:  26
root
 |-- YEAR_MONTH: integer (nullable = true)
 |-- REGIONAL_OFFICE_NAME: string (nullable = true)
 |-- REGIONAL_OFFICE_CODE: string (nullable = true)
 |-- ICB_NAME: string (nullable = true)
 |-- ICB_CODE: string (nullable = true)
 |-- PCO_NAME: string (nullable = true)
 |-- PCO_CODE: string (nullable = true)
 |-- PRACTICE_NAME: string (nullable = true)
 |-- PRACTICE_CODE: string (nullable = true)
 |-- ADDRESS_1: string (nullable = true)
 |-- ADDRESS_2: string (nullable = true)
 |-- ADDRESS_3: string (nullable = true)
 |-- ADDRESS_4: string (nullable = true)
 |-- POSTCODE: string (nullable = true)
 |-- BNF_CHEMICAL_SUBSTANCE: string (nullable = true)
 |-- CHEMICAL_SUBSTANCE_BNF_DESCR: string (nullable = true)
 |-- BNF_CODE: string (nullable = true)
 |-- BNF_DESCRIPTION: string (nullable = true)
 |-- BNF_CHAPTER_PLUS_CODE: string (nullable = true)
 |-- QUANTITY: double (nullable = true)
 |-- ITEMS: integer (nullable = true)
 |-- TOTAL_Q

## Começando os tratamentos:
## 4.	Após a coleta dos dados, separe os dados entre prescribers e prescriptions.

### Prescribers / Prescritores
- Separando o df_spark em Prescribers e as colunas que considerei está relacionado na leitura da documentação.
- Como ultilizarei o pandas e estava tendo problemas com a memoria para processamento, limitei apenas para uma amostra de 150000 linhas
> Prescribers (Prescritores) = PRACTICE_NAME

In [12]:
df_prescribers = df_spark.select("YEAR_MONTH",
                                 "PRACTICE_NAME",
                                 "REGIONAL_OFFICE_NAME",
                                 "ICB_NAME",
                                 "PCO_NAME"
# Aqui tive que optar com limitar a quantidade de linhas, pois ao ultilizar o pandas para salvar o df estava estourando a memoria                                 
                                 ).limit(150000)

df_prescribers.show(50)

+----------+--------------------+--------------------+--------------------+--------------------+
|YEAR_MONTH|       PRACTICE_NAME|REGIONAL_OFFICE_NAME|            ICB_NAME|            PCO_NAME|
+----------+--------------------+--------------------+--------------------+--------------------+
|    202208| BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208| BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208| BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208| BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208| BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208| BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208| BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208| BEACON PRIMARY CA

### Prescriptions / Prescrições
- Separando o df_spark em Prescriptions e as colunas que considerei está relacionado na leitura da documentação.
- Amostra limitada 200000 linhas.
> Prescriptions (Prescrições) = BNF_DESCRIPTION

In [13]:
df_prescriptions = df_spark.select("YEAR_MONTH",
                                   "BNF_DESCRIPTION",
                                   "CHEMICAL_SUBSTANCE_BNF_DESCR",
                                   "QUANTITY",
                                   "ITEMS",
                                   "TOTAL_QUANTITY",
                                   "NIC",
                                   "ACTUAL_COST"
# Mais uma vez limitando a quantidade de linhas por conta da memoria
                                   ).limit(200000)


df_prescriptions.show(50)

+----------+--------------------+----------------------------+--------+-----+--------------+------+-----------+
|YEAR_MONTH|     BNF_DESCRIPTION|CHEMICAL_SUBSTANCE_BNF_DESCR|QUANTITY|ITEMS|TOTAL_QUANTITY|   NIC|ACTUAL_COST|
+----------+--------------------+----------------------------+--------+-----+--------------+------+-----------+
|    202208|K-Lite bandage 10...|          Arm Sling/Bandages|     3.0|    1|           3.0|  3.15|    2.95621|
|    202208|Mepore dressing 7...|        Wound Management ...|     7.0|    1|           7.0|  0.77|      0.732|
|    202208|Mepore dressing 1...|        Wound Management ...|    80.0|    1|          80.0|  17.6|   16.46033|
|    202208|Inadine dressing ...|        Wound Management ...|    10.0|    3|          30.0|  10.2|    9.55713|
|    202208|Inadine dressing ...|        Wound Management ...|     5.0|    1|           5.0|   1.7|    1.60112|
|    202208|Inadine dressing ...|        Wound Management ...|    10.0|    2|          20.0|  10.0|    9

#### Extra:
- Fazendo o fatiamento da coluna 
> YEAR_MONTH em YEAR e MONTH
- Posteriormente vi que não seria necessario a ultilização.


In [15]:
df_YEAR_MONTH_split = df_prescriptions.withColumn('YEAR', func.substring('YEAR_MONTH',1,4))\
.withColumn('MONTH',func.substring('YEAR_MONTH',5,2))

df_YEAR_MONTH_split.show()

+----------+--------------------+----------------------------+--------+-----+--------------+-----+-----------+----+-----+
|YEAR_MONTH|     BNF_DESCRIPTION|CHEMICAL_SUBSTANCE_BNF_DESCR|QUANTITY|ITEMS|TOTAL_QUANTITY|  NIC|ACTUAL_COST|YEAR|MONTH|
+----------+--------------------+----------------------------+--------+-----+--------------+-----+-----------+----+-----+
|    202208|K-Lite bandage 10...|          Arm Sling/Bandages|     3.0|    1|           3.0| 3.15|    2.95621|2022|   08|
|    202208|Mepore dressing 7...|        Wound Management ...|     7.0|    1|           7.0| 0.77|      0.732|2022|   08|
|    202208|Mepore dressing 1...|        Wound Management ...|    80.0|    1|          80.0| 17.6|   16.46033|2022|   08|
|    202208|Inadine dressing ...|        Wound Management ...|    10.0|    3|          30.0| 10.2|    9.55713|2022|   08|
|    202208|Inadine dressing ...|        Wound Management ...|     5.0|    1|           5.0|  1.7|    1.60112|2022|   08|
|    202208|Inadine dres

## 5. Persista os dados da forma que achar melhor:
- Dados persistidos no formado CSV

### Usando o pandas para salvar os DFs de 'Prescriptions' e 'Prescribers'

In [25]:
df_prescriptions.toPandas().to_csv('Warehouse/Mes_08/df_prescriptions.csv', index=False)

df_prescribers.toPandas().to_csv('Warehouse/Mes_08/df_prescribers.csv', index=False)

### Conferindo se os arquivos foram corretamente exportados e armazenados 


In [28]:
# Lendo a amostra dos arquivos 
df_check_prescriptions = spark.read.csv(r'Warehouse/Mes_08/df_prescriptions.csv', sep = ',', inferSchema=True, header=True)

df_check_prescriptions.show()

+----------+--------------------+----------------------------+--------+-----+--------------+-----+-----------+
|YEAR_MONTH|     BNF_DESCRIPTION|CHEMICAL_SUBSTANCE_BNF_DESCR|QUANTITY|ITEMS|TOTAL_QUANTITY|  NIC|ACTUAL_COST|
+----------+--------------------+----------------------------+--------+-----+--------------+-----+-----------+
|    202208|K-Lite bandage 10...|          Arm Sling/Bandages|     3.0|    1|           3.0| 3.15|    2.95621|
|    202208|Mepore dressing 7...|        Wound Management ...|     7.0|    1|           7.0| 0.77|      0.732|
|    202208|Mepore dressing 1...|        Wound Management ...|    80.0|    1|          80.0| 17.6|   16.46033|
|    202208|Inadine dressing ...|        Wound Management ...|    10.0|    3|          30.0| 10.2|    9.55713|
|    202208|Inadine dressing ...|        Wound Management ...|     5.0|    1|           5.0|  1.7|    1.60112|
|    202208|Inadine dressing ...|        Wound Management ...|    10.0|    2|          20.0| 10.0|    9.34542|
|

In [29]:
# Lendo a amostra dos arquivos
df_check_prescribers = spark.read.csv(r'Warehouse/Mes_08/df_prescribers.csv', sep = ',', inferSchema=True, header=True)

df_check_prescribers.show()

+----------+-------------------+--------------------+--------------------+--------------------+
|YEAR_MONTH|      PRACTICE_NAME|REGIONAL_OFFICE_NAME|            ICB_NAME|            PCO_NAME|
+----------+-------------------+--------------------+--------------------+--------------------+
|    202208|BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208|BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208|BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208|BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208|BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208|BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208|BEACON PRIMARY CARE|          NORTH WEST|NHS LANCASHIRE AN...|NHS LANCASHIRE AN...|
|    202208|BEACON PRIMARY CARE|        

## 6. Gere scripts que atendam as solicitações abaixo:

- Aqui optei por ultilizar SQL por ter maior dominio, ao invez de mesclar com o PySpark.

#### Criando a View que ultilizarei nas consultas SQL:

In [32]:
df_spark.createOrReplaceTempView("query")

### 1º Query:
- a. Crie um dataframe contendo os 10 principais produtos químicos prescritos por região.

In [33]:
df_query1_sql = spark.sql("""
with quimico as(
    SELECT 
        REGIONAL_OFFICE_NAME as Regiao,
        CHEMICAL_SUBSTANCE_BNF_DESCR as Substancia,
        sum(TOTAL_QUANTITY) as Total
    FROM query
    GROUP BY 1,2),
top10 as (
    select *,
    row_number() over (partition by Regiao order by Total desc, Substancia ) as rank
    from quimico)

select Rank,
       Regiao,
       Substancia,
       Total
from top10
where rank <= 10
order by Regiao, Total desc;
""")


#### Setando valores float sem notação científica
- Por padrão o pandas vem com notação cientifica. Para uma melhor visualização, optei por alterar

In [36]:
pd.options.display.float_format = '{:.2f}'.format

### Extra:
> Como já informei anteriormente, não gosto da visualização com o pyspark, por ser tratar de um DF relativamente pequeno, optei por utilizar o pandas.


In [35]:
# Conta todas as linhas contidas na query
## all_lines = df_query1_sql.count() 

# Imprime as linhas resultantes
## df_query1_sql.show(all_lines) 

+----+--------------------+--------------------+------------+
|Rank|              Regiao|          Substancia|       Total|
+----+--------------------+--------------------+------------+
|   1|     EAST OF ENGLAND|   Enteral nutrition| 2.0406218E8|
|   2|     EAST OF ENGLAND|          Emollients| 3.9584968E7|
|   3|     EAST OF ENGLAND|Other food for sp...| 2.5139729E7|
|   4|     EAST OF ENGLAND|Metformin hydroch...| 1.9865835E7|
|   5|     EAST OF ENGLAND|         Paracetamol| 1.9459784E7|
|   6|     EAST OF ENGLAND|        Atorvastatin| 1.8177977E7|
|   7|     EAST OF ENGLAND|Other emollient p...|  1.675578E7|
|   8|     EAST OF ENGLAND|Co-codamol (Codei...| 1.5464052E7|
|   9|     EAST OF ENGLAND|Alginic acid comp...| 1.3341929E7|
|  10|     EAST OF ENGLAND|Levothyroxine sodium| 1.3008007E7|
|   1|              LONDON|   Enteral nutrition|2.99867575E8|
|   2|              LONDON|          Emollients|  6.753213E7|
|   3|              LONDON|Metformin hydroch...|  3.193982E7|
|   4|  

#### Retirando o limitador maximo de linhas (Doido pra quebrar  o pandas kkkk)

In [41]:
pd.set_option('display.max_rows', None)

### Exportando o resultado para um csv e conferindo a disponibilidade / armazenamento
- No resultado da query optei por mostrar um "Rank" para oferecer mais clareza nos dados coletados

In [44]:
df_query1_sql.toPandas().to_csv('Warehouse/Mes_08/df_query1_sql.csv', index=False)
pd.read_csv('Warehouse/Mes_08/df_query1_sql.csv')

Rank                    Regiao  \
0      1           EAST OF ENGLAND   
1      2           EAST OF ENGLAND   
2      3           EAST OF ENGLAND   
3      4           EAST OF ENGLAND   
4      5           EAST OF ENGLAND   
5      6           EAST OF ENGLAND   
6      7           EAST OF ENGLAND   
7      8           EAST OF ENGLAND   
8      9           EAST OF ENGLAND   
9     10           EAST OF ENGLAND   
10     1                    LONDON   
11     2                    LONDON   
12     3                    LONDON   
13     4                    LONDON   
14     5                    LONDON   
15     6                    LONDON   
16     7                    LONDON   
17     8                    LONDON   
18     9                    LONDON   
19    10                    LONDON   
20     1                  MIDLANDS   
21     2                  MIDLANDS   
22     3                  MIDLANDS   
23     4                  MIDLANDS   
24     5                  MIDLANDS   
25     6                  MIDLANDS   
26     7                  MIDLANDS   
27     8                  MIDLANDS   
28     9                  MIDLANDS   
29    10                  MIDLANDS   
30     1  NORTH EAST AND YORKSHIRE   
31     2  NORTH EAST AND YORKSHIRE   
32     3  NORTH EAST AND YORKSHIRE   
33     4  NORTH EAST AND YORKSHIRE   
34     5  NORTH EAST AND YORKSHIRE   
35     6  NORTH EAST AND YORKSHIRE   
36     7  NORTH EAST AND YORKSHIRE   
37     8  NORTH EAST AND YORKSHIRE   
38     9  NORTH EAST AND YORKSHIRE   
39    10  NORTH EAST AND YORKSHIRE   
40     1                NORTH WEST   
41     2                NORTH WEST   
42     3                NORTH WEST   
43     4                NORTH WEST   
44     5                NORTH WEST   
45     6                NORTH WEST   
46     7                NORTH WEST   
47     8                NORTH WEST   
48     9                NORTH WEST   
49    10                NORTH WEST   
50     1                SOUTH EAST   
51     2                SOUTH EAST   
52     3                SOUTH EAST   
53     4                SOUTH EAST   
54     5                SOUTH EAST   
55     6                SOUTH EAST   
56     7                SOUTH EAST   
57     8                SOUTH EAST   
58     9                SOUTH EAST   
59    10                SOUTH EAST   
60     1                SOUTH WEST   
61     2                SOUTH WEST   
62     3                SOUTH WEST   
63     4                SOUTH WEST   
64     5                SOUTH WEST   
65     6                SOUTH WEST   
66     7                SOUTH WEST   
67     8                SOUTH WEST   
68     9                SOUTH WEST   
69    10                SOUTH WEST   
70     1              UNIDENTIFIED   
71     2              UNIDENTIFIED   
72     3              UNIDENTIFIED   
73     4              UNIDENTIFIED   
74     5              UNIDENTIFIED   
75     6              UNIDENTIFIED   
76     7              UNIDENTIFIED   
77     8              UNIDENTIFIED   
78     9              UNIDENTIFIED   
79    10              UNIDENTIFIED   

                                    Substancia        Total  
0                            Enteral nutrition 204062180.00  
1                                   Emollients  39584968.00  
2     Other food for special diet preparations  25139729.00  
3                      Metformin hydrochloride  19865835.00  
4                                  Paracetamol  19459784.00  
5                                 Atorvastatin  18177977.00  
6                 Other emollient preparations  16755780.00  
7   Co-codamol (Codeine phosphate/paracetamol)  15464052.00  
8           Alginic acid compound preparations  13341929.00  
9                         Levothyroxine sodium  13008007.00  
10                           Enteral nutrition 299867575.00  
11                                  Emollients  67532130.00  
12                     Metformin hydrochloride  31939820.00  
13                Other emollient preparations  30713300.

### 2º query
- b. Quais produtos químicos prescritos tiveram a maior somatória de custos por mês? Liste os 10 primeiros.
- Os custos são dados em Libras esterlinas (£)
- Com mais tempo seria interessante implementa um web scraping para converter em R$ pela cotação do dia.

In [45]:
df_query2_sql = spark.sql("""
with principal as(
    SELECT 
        YEAR_MONTH as ano_mes,
        CHEMICAL_SUBSTANCE_BNF_DESCR as Substancia,
        round(sum(NIC),2) as Total
    FROM query
    GROUP BY 1,2),
top10 as (
    select *,
    row_number() over (partition by ano_mes order by Total desc, Substancia ) as rank
    from principal)

select Rank,
       ano_mes,
       Substancia,
       Total
from top10
where rank <= 10
order by ano_mes, Total desc;
""")

In [46]:
# Mostrando como seria a visualização pelo PySpark
#df_query2_sql.show()

+----+-------+--------------------+-------------+
|Rank|ano_mes|          Substancia|        Total|
+----+-------+--------------------+-------------+
|   1| 202208|            Apixaban|3.682613654E7|
|   2| 202208|   Enteral nutrition|2.723454533E7|
|   3| 202208|Beclometasone dip...|2.568696516E7|
|   4| 202208|         Rivaroxaban| 2.06129727E7|
|   5| 202208|           Catheters|1.331314274E7|
|   6| 202208|Detection Sensor ...| 1.28100181E7|
|   7| 202208|            Edoxaban| 1.11347285E7|
|   8| 202208|       Dapagliflozin|1.096375015E7|
|   9| 202208|Wound Management ...|1.073179036E7|
|  10| 202208|          Budesonide|1.058631729E7|
+----+-------+--------------------+-------------+



### Exportando o resultado para um csv e conferindo a disponibilidade / armazenamento

In [47]:
df_query2_sql.toPandas().to_csv('Warehouse/Mes_08/df_query2_sql.csv', index=False)
pd.read_csv('df_query2_sql.csv')

Rank  ano_mes                                Substancia       Total
0     1   202208                                  Apixaban 36826136.54
1     2   202208                         Enteral nutrition 27234545.33
2     3   202208                Beclometasone dipropionate 25686965.16
3     4   202208                               Rivaroxaban 20612972.70
4     5   202208                                 Catheters 13313142.74
5     6   202208  Detection Sensor Interstitial Fluid/Gluc 12810018.10
6     7   202208                                  Edoxaban 11134728.50
7     8   202208                             Dapagliflozin 10963750.15
8     9   202208        Wound Management & Other Dressings 10731790.36
9    10   202208                                Budesonide 10586317.29

### 3º Query
- c. Quais são as precrições mais comuns?
- Como o desafio não especifica um limite, opto por uma amostra listando as 100 primeiras.

In [53]:
df_query3_sql = spark.sql("""
SELECT
    BNF_DESCRIPTION as Prescricao,
    sum(ITEMS) as Quantidade
FROM query
GROUP BY 1 
order by 2 desc
limit 100;
--Caso necessite uma amostra maior é só ajustar o limit
""")

### Exportando o resultado para um csv e conferindo a disponibilidade / armazenamento

In [54]:
df_query3_sql.toPandas().to_csv('Warehouse/Mes_08/df_query3_sql.csv', index=False)
pd.read_csv('Warehouse/Mes_08/df_query3_sql.csv')

Prescricao  Quantidade
0           Omeprazole 20mg gastro-resistant capsules     2659334
1                           Atorvastatin 20mg tablets     2349300
2                              Amlodipine 5mg tablets     1748969
3         Lansoprazole 30mg gastro-resistant capsules     1633842
4                           Atorvastatin 40mg tablets     1309360
5                    Aspirin 75mg dispersible tablets     1304558
6                             Metformin 500mg tablets     1191745
7                           Paracetamol 500mg tablets     1190101
8                             Amlodipine 10mg tablets     1148598
9         Lansoprazole 15mg gastro-resistant capsules     1023698
10          Levothyroxine sodium 100microgram tablets      990198
11                            Sertraline 50mg tablets      973841
12                           Clopidogrel 75mg tablets      930364
13                           Bisoprolol 2.5mg tablets      889385
14           Levothyroxine sodium 50microgram tablets      865053
15                         Amitriptyline 10mg tablets      861663
16                             Ramipril 10mg capsules      855539
17           Levothyroxine sodium 25microgram tablets      839955
18                           Sertraline 100mg tablets      835261
19     Salbutamol 100micrograms/dose inhaler CFC free      829106
20                             Folic acid 5mg tablets      748881
21                           Simvastatin 40mg tablets      702114
22  Tamsulosin 400microgram modified-release capsules      690876
23                            Ramipril 2.5mg capsules      685900
24                            Citalopram 20mg tablets      670625
25                          Atorvastatin 80mg tablets      667481
26                              Ramipril 5mg capsules      659493
27                            Furosemide 40mg tablets      588281
28                          Bisoprolol 1.25mg tablets      570007
29                          Atorvastatin 10mg tablets      558850
30                  Bendroflumethiazide 2.5mg tablets      553879
31                           Fluoxetine 20mg capsules      551744
32                           Simvastatin 20mg tablets      545917
33                             Bisoprolol 5mg tablets      501836
34                               Apixaban 5mg tablets      490539
35                      Co-codamol 30mg/500mg tablets      434432
36                       Alendronic acid 70mg tablets      432401
37                             Tramadol 50mg capsules      397025
38                             Naproxen 500mg tablets      391605
39               Ventolin 100micrograms/dose Evohaler      380252
40                           Mirtazapine 15mg tablets      365821
41                             Losartan 100mg tablets      363843
42                            Furosemide 20mg tablets      362214
43                          Gabapentin 300mg capsules      360006
44                            Citalopram 10mg tablets      353998
45  Fostair 100micrograms/dose / 6micrograms/dose ...      352340
46                              Losartan 50mg tablets      351186
47                          Allopurinol 100mg tablets      345313
48                            Finasteride 5mg tablets      343927
49                          Zapain 30mg/500mg tablets      337424
50                           Prednisolone 5mg tablets      337027
51                            Gliclazide 80mg tablets      333840
52                                Senna 7.5mg tablets      331707
53                     Ferrous fumarate 210mg tablets      327034
54                           Indapamide 2.5mg tablets      319425
55                      Flucloxacillin 500mg capsules      315313
56                         Amoxicillin 500mg capsules      311734
57     Nitrofurantoin 100mg modified-release capsules      308035
58                           Montelukast 10mg tablets      305891
59                           Mirtazapine 30mg tablets      297389
60               

### 4º query
- d. Qual produto químico é mais prescrito por cada prescriber?


In [55]:
df_query4_sql = spark.sql("""
with test as(
    SELECT 
        PRACTICE_NAME as Prescriber,
        CHEMICAL_SUBSTANCE_BNF_DESCR as Substancia,
        sum(ITEMS) as Quantidade
    FROM query
    GROUP BY 1,2),
top1 as (
    select *,
    row_number() over (partition by prescriber order by Quantidade desc, Substancia ) as qtd
    from test)

select Prescriber,
       Substancia,
       Quantidade
from top1
where qtd = 1
order by prescriber, Quantidade desc;

""")

### Exportando o resultado para um csv e conferindo a disponibilidade / armazenamento

In [56]:
df_query4_sql.toPandas().to_csv('Warehouse/Mes_08/df_query4_sql.csv', index=False)
pd.read_csv('Warehouse/Mes_08/df_query4_sql.csv')

Prescriber  \
0                  (FRACTURE CLINIC) NORTH OOH   
1     (IRLAM) SALFORD CARE CTRS MEDICAL PRACTI   
2           (OUT PATIENT DEPARTMENT) NORTH OOH   
3           0-19 EAST CHESHIRE HEALTH VISITORS   
4        0-19 PUBLIC HEALTH SERVICE HARTLEPOOL   
5                                1 TO 1 CENTRE   
6                    1/MONTON MEDICAL PRACTICE   
7                   1/SALFORD MEDICAL PRACTICE   
8                               15 SEFTON ROAD   
9                            168 MEDICAL GROUP   
10                  19 BEAUMONT STREET SURGERY   
11                             240 WEXHAM ROAD   
12                                27@NORTHGATE   
13                                28@NORTHGATE   
14          3/LOWER BROUGHTON MEDICAL PRACTICE   
15        3/SPRINGFIELD HOUSE MEDICAL PRACTICE   
16                     301 EAST STREET SURGERY   
17                           3D MEDICAL CENTRE   
18                            3VH RHEUMATOLOGY   
19                                   3W HEALTH   
20                    4 SEASONS MEDICAL CENTRE   
21                                 42 KINGSWAY   
22                    49 MARINE AVENUE SURGERY   
23              7 DAY ACCESS LITTLEBOROUGH HUB   
24                   7 DAY ACCESS MIDDLETON HC   
25                    7 DAY ACCESS PHOENIX HUB   
26         7 DAY ACCESS ROCHDALE INFIRMARY HUB   
27                            7 DAY GP SERVICE   
28                     8 TO 8 TOP-UP HUB ERITH   
29                       8 TO 8 TOP-UP HUB QMH   
30               A & E NON MEDICAL PRESCRIBERS   
31                                     A&E GPS   
32                            ABBAMOOR SURGERY   
33                   ABBEY DALE MEDICAL CENTRE   
34                  ABBEY FIELD MEDICAL CENTRE   
35               ABBEY GRANGE MEDICAL PRACTICE   
36                ABBEY HOUSE MEDICAL PRACTICE   
37                   ABBEY MEADS MEDICAL PRACT   
38                        ABBEY MEDICAL CENTRE   
39                         ABBEY MEDICAL GROUP   
40                      ABBEY MEDICAL PRACTICE   
41                 ABBEY ROAD MEDICAL PRACTICE   
42                          ABBEY ROAD SURGERY   
43                               ABBEY SURGERY   
44                          ABBEY WOOD SURGERY   
45                   ABBEYSLADE PMS (DR CHAND)   
46                           ABBEYVIEW SURGERY   
47                           ABBEYWELL SURGERY   
48                      ABBOTS BROMLEY SURGERY   
49                   ABBOTSWOOD MEDICAL CENTRE   
50                  ABBOTTSWOOD MEDICAL CENTRE   
51                  ABERCROMBY FAMILY PRACTICE   
52                          ABERFELDY PRACTICE   
53                     ABERNETHY HOUSE SURGERY   
54               ABH MANCHESTER & TRAFFORD CDS   
55          ABINGDON FAMILY HEALTH CARE CENTRE   
56                     ABINGTON MEDICAL CENTRE   
57                       ABINGTON PARK SURGERY   
58                 ABOUT HEALTH LN DERMATOLOGY   
59                            ABOUT HEALTH LTD   
60                             ABRIDGE SURGERY   
61                  ACCIDENT AND EMERGENCY WWL   
62                                      ACCT 2   
63                                 ACE LTD OOH   
64                                 ACHE CLINIC   
65             ACHIEVE BOLTON RECOVERY SERVICE   
66                       ACKLAM MEDICAL CENTRE   
67                    ACLE MEDICAL PARTNERSHIP   
68          ACMH-INTENSIVE HOME TREATMENT TEAM   
69                 ACOCKS GREEN MEDICAL CENTRE   
70                        ACORN MEDICAL CENTRE   
71                      ACORN MEDICAL PRACTICE   
72                              ACORN PRACTICE   
73                               ACORN SURGERY   
74                   ACORNS CHILDREN'S HOSPICE   
75            ACORNS CHILDRENS HOSPICE WALSALL   
76                                ACRE SURGERY   
77                           ACREFIELD SURGERY   
78                      ACTIVE RECOVERY (CICS)   
79                   ACTON LANE MEDI

### 5º Query
e. Quantos prescribers foram adicionados no ultimo mês? 

## Por ultilizar um metodo diferente, optei por deixar para o final...

### 6º query
- f. Quais prescribers atuam em mais de uma região? Ordene por quantidade de regiões antendidas.

- Aqui acrescentei qual seria a região mais atendida.
- Pode ser ajustado no 'where top = "n" ' para apresentar em sequencia qual seria a 2º,3º,etc.
- Retirei os UNIDENTIFIED DOCTORS, por se tratar de um dado impreciso e ser o que tinha o maior numero de regiões (8 ao total).


In [58]:
df_query6_sql = spark.sql(
    """with regiao as ( 
    SELECT
        PRACTICE_NAME as Prescribers,
        REGIONAL_OFFICE_NAME as Regiao_principal
    FROM query
    group by 1,2),
filtro as(
    select *,
    row_number() over (partition by Prescribers order by Regiao_principal) as Qtd_Regioes,
    rank() over (partition by Prescribers order by Regiao_principal desc) as top 
    from regiao)

select Prescribers,
       Regiao_principal,
       Qtd_Regioes
from filtro
where top = 1 and Qtd_Regioes >= 2 and Prescribers not in ('UNIDENTIFIED DOCTORS')
order by Qtd_Regioes desc, Prescribers;
""")

### Exportando o resultado para um csv e conferindo a disponibilidade / armazenamento

In [59]:
df_query6_sql.toPandas().to_csv('Warehouse/Mes_08/df_query6_sql.csv', index=False)
pd.read_csv('Warehouse/Mes_08/df_query6_sql.csv')

Prescribers          Regiao_principal  \
0                            VILLAGE SURGERY                SOUTH WEST   
1                        HIGH STREET SURGERY                SOUTH EAST   
2                            CENTRAL SURGERY                NORTH WEST   
3                          RIVERSIDE SURGERY                SOUTH EAST   
4                     TRINITY MEDICAL CENTRE                SOUTH EAST   
5                 BIRCHWOOD MEDICAL PRACTICE                SOUTH WEST   
6              COMMUNITY DERMATOLOGY SERVICE                SOUTH WEST   
7                      COMMUNITY ENT SERVICE                NORTH WEST   
8                          HIGHFIELD SURGERY                SOUTH EAST   
9                           KINGSWAY SURGERY                NORTH WEST   
10                           ORCHARD SURGERY                SOUTH EAST   
11                         PARK LANE SURGERY                NORTH WEST   
12                       PARK MEDICAL CENTRE                NORTH WEST   
13                       THE VILLAGE SURGERY                SOUTH EAST   
14                         WOODLANDS SURGERY                SOUTH EAST   
15                      ABBEY MEDICAL CENTRE                SOUTH EAST   
16                        ADULT ADHD SERVICE                SOUTH EAST   
17                          ASHCROFT SURGERY                SOUTH EAST   
18                   BROADWAY MEDICAL CENTRE                NORTH WEST   
19                    CENTRAL MEDICAL CENTRE                  MIDLANDS   
20                       CHURCH LANE SURGERY  NORTH EAST AND YORKSHIRE   
21                       CHURCH VIEW SURGERY                SOUTH WEST   
22                COMMUNITY DIABETES SERVICE                NORTH WEST   
23                       GROVE HOUSE SURGERY                SOUTH WEST   
24                      GROVE MEDICAL CENTRE                SOUTH EAST   
25                             GROVE SURGERY                SOUTH WEST   
26                         HILLCREST SURGERY                SOUTH WEST   
27                         KINGSWOOD SURGERY                SOUTH WEST   
28                         LIME TREE SURGERY                SOUTH EAST   
29                        MANOR ROAD SURGERY                SOUTH EAST   
30                          OAKFIELD SURGERY                SOUTH EAST   
31                  ORCHARD MEDICAL PRACTICE                NORTH WEST   
32                   PALLIATIVE CARE SERVICE                NORTH WEST   
33                              PARK SURGERY                SOUTH EAST   
34                         PARK VIEW SURGERY                NORTH WEST   
35                   PARKSIDE MEDICAL CENTRE                  MIDLANDS   
36                     PRIORY MEDICAL CENTRE                NORTH WEST   
37                       QUEENS ROAD SURGERY  NORTH EAST AND YORKSHIRE   
38                   RICHMOND MEDICAL CENTRE                NORTH WEST   
39                       SPRINGFIELD SURGERY                SOUTH EAST   
40                  ST ALBANS MEDICAL CENTRE                SOUTH WEST   
41                 ST ANDREWS MEDICAL CENTRE                SOUTH EAST   
42                         ST MARY'S SURGERY                SOUTH EAST   
43                      STATION ROAD SURGERY                SOUTH EAST   
44                        THE AVENUE SURGERY                SOUTH EAST   
45                 THE GRANGE MEDICAL CENTRE  NORTH EAST AND YORKSHIRE   
46                  THE LIMES MEDICAL CENTRE                SOUTH EAST   
47                           THE NEW SURGERY                SOUTH EAST   
48                               THE SURGERY                NORTH WEST   
49                THE VILLAGE MEDICAL CENTRE                SOUTH EAST   
50                   URGENT TREATMENT CENTRE                  MIDLANDS   
51                   VICTORIA MEDICAL CENTRE                SOUTH EAST   
52                     VICTORIA ROAD SURGERY                SOUTH EAST   
53                       WHITE HOUSE 

### 7º query
- g. Qual o preço médio dos químicos prescritos em no ultimo mês coletado?
- Aqui por ter sido um query mais simples, optei por acrescentar algumas informações extras como:
- Os custos são dados em Libras esterlinas (£)

1. Valor_Medio_liquido = Valor Com descontos totais 
2. Maior_valor = O maior valor encontrado do quimico
3. Menor_valor = O menor valor encontrado do quimico



In [60]:
df_query7_sql = spark.sql("""
SELECT 
    CHEMICAL_SUBSTANCE_BNF_DESCR as Substancia,
    round(avg(NIC),2) as Valor_Medio_bruto,
    round(avg(ACTUAL_COST),2) as Valor_Medio_liquido,
    round(max(ACTUAL_COST),2) as Maior_valor,
    round(min(ACTUAL_COST),2) as Menor_valor
FROM query
where CHEMICAL_SUBSTANCE_BNF_DESCR != ""
GROUP BY 1
order by 1,4 desc
""")

### Exportando o resultado para um csv e conferindo a disponibilidade / armazenamento

In [62]:
# Exportando o resultado para um csv
df_query7_sql.toPandas().to_csv('Warehouse/Mes_08/df_query7_sql.csv', index=False)
pd.read_csv('Warehouse/Mes_08/df_query7_sql.csv')

Substancia  Valor_Medio_bruto  \
0                               Abacavir and lamivudine               6.33   
1                                     Absorbent Cottons               9.24   
2                                   Acamprosate calcium              40.76   
3                                              Acarbose              34.02   
4                              Acebutolol hydrochloride              36.28   
5                                           Aceclofenac              10.35   
6                                         Acenocoumarol               6.91   
7                                         Acetazolamide              12.15   
8                                           Acetic acid               8.12   
9                                        Acetylcysteine              55.97   
10                                            Aciclovir               8.85   
11                                             Acipimox              49.65   
12                                            Acitretin              59.15   
13                                   Aclidinium bromide             107.17   
14                        Aclidinium bromide/formoterol             116.78   
15                                       Acne Treatment              19.50   
16                                          Acrivastine              26.30   
17                                           Adalimumab             413.77   
18                                            Adapalene              30.46   
19                       Adapalene and benzoyl peroxide              43.65   
20                                   Adefovir dipivoxil             252.22   
21                   Adhesive (Pastes/Sprays/Solutions)              19.91   
22                   Adhesive Discs/Rings/Pads/Plasters              59.34   
23              Adhesive Dressing Remover Ster Silicone              34.08   
24             Adhesive Removers (Sprays/Liquids/Wipes)              33.37   
25                                           Adrenaline             137.79   
26                                          Agomelatine              40.72   
27                                          Albendazole             139.09   
28                           Alclometasone dipropionate              29.51   
29                                              Alcohol               2.86   
30                                      Alendronic acid             353.26   
31                       Alendronic acid/colecalciferol              43.16   
32                                         Alfacalcidol              20.98   
33                             Alfentanil hydrochloride              18.06   
34                              Alfuzosin hydrochloride              26.68   
35                   Alginic acid compound preparations              18.96   
36                                 Alimemazine tartrate             381.87   
37                                           Alirocumab             451.50   
38                                            Aliskiren              54.49   
39                                         Alitretinoin             538.60   
40                                        Alkyl sulfate               3.32   
41                                       Alkyl sulphate              10.39   
42                                          Allopurinol              14.19   
43                                          Almotriptan              37.31   
44                                           Alogliptin             235.34   
45                                 Alogliptin/metformin             113.03   
46                                          Alprostadil              70.15   
47     Aluminium and magnesium and activated simeticone              10.41   
48               Aluminium and magnesium and oxetacaine              38.04   
49                                   Aluminium chloride               6.28   
50                                  Aluminium hydroxide            

### 8º query
- h. Gere uma tabela que contenha apenas a prescrição de maior valor de cada "usuário".
- P.s.: Aqui interpletei 
    > Usuario > Prescriber

In [63]:
df_query8_sql = spark.sql("""
with valor as(
    SELECT 
        PCO_NAME as Prescriber,
        CHEMICAL_SUBSTANCE_BNF_DESCR as Substancia,
        round(max(ACTUAL_COST),2) as Maior_valor
    FROM query
    GROUP BY 1,2),
top1 as (
    select *,
    row_number() over (partition by prescriber order by Maior_valor desc, Substancia ) as qtd
    from valor )

select Prescriber,
       Substancia,
       Maior_valor
from top1
where qtd = 1
order by prescriber, Maior_valor desc;
--order by Maior_valor desc, prescriber; só para reordenar por maior valor
""")

### Exportando o resultado para um csv e conferindo a disponibilidade / armazenamento


In [64]:
df_query8_sql.toPandas().to_csv('Warehouse/Mes_08/df_query8_sql.csv', index=False)
pd.read_csv('Warehouse/Mes_08/df_query8_sql.csv')

Prescriber  \
0                                ABOUT HEALTH   
1               AIREDALE NHS FOUNDATION TRUST   
2                ALLIANCE FOR BETTER CARE CIC   
3    ASHFORD & ST PETER'S HOSPITALS NHS FOUND   
4    BERKSHIRE HEALTHCARE NHS FOUNDATION TRUS   
5    BIRMINGHAM COMMUNITY HEALTHCARE NHS FOUN   
6    BIRMINGHAM WOMEN'S AND CHILDREN'S NHS FO   
7    BLACK COUNTRY HEALTHCARE NHS FOUNDATION    
8                              BMI HEALTHCARE   
9                 BOLTON NHS FOUNDATION TRUST   
10   BRADFORD DISTRICT CARE NHS FOUNDATION TR   
11   BRIDGEWATER COMMUNITY HEALTHCARE NHS FOU   
12            BRISDOC HEALTHCARE SERVICES LTD   
13                         BROMLEY HEALTHCARE   
14       BUCKINGHAMSHIRE HEALTHCARE NHS TRUST   
15          BURY METROPOLITAN BOROUGH COUNCIL   
16   CENTRA AND NORTH WEST LONDON NHS FOUNDAT   
17   CENTRAL LONDON COMMUNITY HEALTHCARE NHS    
18                         CHANGE, GROW, LIVE   
19                       CHARING PRACTICE LTD   
20   CHESHIRE & WIRRAL PARTNERSHIP NHS FOUNDA   
21                                     CIRCLE   
22           CITY HEALTH CARE PARTNERSHIP CIC   
23    COASTAL HEALTH GP PROVIDER ORGANISATION   
24                         COMMUNITAS CLINICS   
25        CONCORDIA COMMUNITY OUTPATIENTS LTD   
26                     CONNECT HEALTH LIMITED   
27   CONSULTANT EYE SURGEONS PARTNERSHIP (CAN   
28               COUNTESS MOUNTBATTEN HOSPICE   
29   COVENTRY AND WARWICKSHIRE PARTNERSHIP NH   
30                                  CRANSTOUN   
31                                 CSH SURREY   
32   CUMBRIA,NORTHUMBERLAND,TYNE AND WEAR NHS   
33                 DARLINGTON BOROUGH COUNCIL   
34                         DELPHI MEDICAL LTD   
35   DERBYSHIRE COMMUNITY HEALTH SERVICES NHS   
36   DERBYSHIRE HEALTHCARE NHS FOUNDATION TRU   
37          DMC COMMUNITY OUTPATIENT SERVICES   
38                      DURHAM COUNTY COUNCIL   
39   EAST KENT HOSPITALS UNIVERSITY NHS FOUND   
40       EAST LANCASHIRE MEDICAL SERVICES LTD   
41   EAST SUFFOLK AND NORTH ESSEX NHS FOUNDAT   
42           EAST SUSSEX HEALTHCARE NHS TRUST   
43              EDP DRUG AND ALCOHOL SERVICES   
44   EPSOM AND ST HELIER UNIVERSITY HOSPITALS   
45   ESSEX PARTNERSHIP UNIVERSITY NHS FOUNDAT   
46             FAVERSHAM MEDICAL PRACTICE MIU   
47                                  FRAMEWORK   
48     GATESHEAD METROPOLITAN BOROUGH COUNCIL   
49    GLOUCESTERSHIRE CARE SERVICES NHS TRUST   
50   GLOUCESTERSHIRE HEALTH AND CARE NHS FOUN   
51   GREAT WESTERN HOSPITALS NHS FOUNDATION T   
52   GREATER MANCHESTER MENTAL HEALTH NHS FOU   
53                      GREENBROOK HEALTHCARE   
54                             GTD HEALTHCARE   
55   GUY'S AND ST THOMAS' NHS FOUNDATION TRUS   
56   HARROGATE AND DISTRICT NHS FOUNDATION TR   
57                 HARTLEPOOL BOROUGH COUNCIL   
58                              HCRG CARE LTD   
59                     HCRG CARE SERVICES LTD   
60                     HEALTHHARMONIE LIMITED   
61                                       HERE   
62   HEREFORDSHIRE AND WORCESTERSHIRE HEALTH    
63                  HERNE BAY HEALTH CARE LTD   
64          HERTFORDSHIRE COMMUNITY NHS TRUST   
65   HOMERTON UNIVERSITY HOSPITAL NHS FOUNDAT   
66                                  HUMANKIND   
67       HUMBER TEACHING NHS FOUNDATION TRUST   
68                           INHEALTH LIMITED   
69                     INTEGRATED CARE 24 LTD   
70                                     ISIGHT   
71                    ISLE OF WIGHT NHS TRUST   
72   KENT COMMUNITY HEALTH NHS FOUNDATION TRU   
73   KING'S COLLEGE HOSPITAL NHS FOUNDATION T   
74                           KIRKLEES COUNCIL   
75   LANCASHIRE & SOUTH CUMBRIA NHS FOUNDATIO   
76   LANCASTER HOUSE CONSULTING DIAGNOSTICS S   
77                         LEEDS CITY COUNCIL   
78       LEEDS COMMUNITY HEALTHCARE NHS TRUST   
79           LEWISHAM AND GREENWICH NHS TRUST   
80   LINCOLNSHIRE AND DISTRICTS MEDICAL SERVI   
81   LINCOLNSHIRE

---
# Aqui indico verificar o notebook 'Rotina_mensal' para entender melhor o que foi informado a respeito da extração das amostras utilizadas aqui.
- [Rotina_mensal](Rodina_Mensal.ipynb)
---
## Retomando a 5º Query
- e. Quantos Prescribers foram adicionados no ultimo mês? 


### Com os arquivos já extraidos seguimos da seguinte formar:
- Criação de 2 DFs referentes a cada mês (agosto e junho)

In [66]:
df_amostra_ultimo = spark.read.csv(r'C:\Users\arthu\Desktop\EPD_202208-00.csv', sep = ',', inferSchema=True, header=True)
df_amostra_anterior = spark.read.csv(r'C:\Users\arthu\Desktop\EPD_202207-00.csv', sep = ',', inferSchema=True, header=True)

#### Filtro as colunas que julgo apenas necessarias:
- YEAR_MONTH
- PRACTICE_NAME

In [70]:
df_filtro_1 = df_amostra_anterior.select('YEAR_MONTH','PRACTICE_NAME')
df_filtro_2 = df_amostra_ultimo.select('YEAR_MONTH','PRACTICE_NAME')

#### Faço a união dos valores distindos de cada DF:
- Dessa forma serão unidos apenas os valores unicos referentes a cada mês.

In [71]:
add_no_mes = df_filtro_1.union(df_filtro_2).distinct()

#### Criando a View SQL para proxima consulta:

In [73]:
add_no_mes.createOrReplaceTempView("query_amostra")

### Exportando o resultado para um csv e conferindo a disponibilidade / armazenamento

In [75]:
add_no_mes.toPandas().to_csv('Warehouse/Mes_08/add_no_mes.csv', index=False)
add_no_mes = pd.read_csv(r'Warehouse/Mes_08/add_no_mes.csv')
add_no_mes

YEAR_MONTH                             PRACTICE_NAME
0          202207                   WATERLOO MEDICAL CENTRE
1          202207                     HELSBY STREET MED/CTR
2          202207                GTD HEALTHCARE CHORLEY OOH
3          202207                     BLUNDELLSANDS SURGERY
4          202207                                HMP HEWELL
5          202207                     MERIDIAN HEALTH GROUP
6          202207               MATERNAL MENTAL HEALTH TEAM
7          202207             HEREFORDSHIRE MH OA COMMUNITY
8          202207                           HONITON SURGERY
9          202207                   MOORDOWN MEDICAL CENTRE
10         202207                          WARMDENE SURGERY
11         202207                  PARK ROAD GROUP PRACTICE
12         202207                          HILLFOOT SURGERY
13         202207                   DR JJ MCPEAKES PRACTICE
14         202207               MARITIME HEALTH PARTNERSHIP
15         202207               DARTFORD EAST HEALTH CENTRE
16         202207     BRIGSTOCK & SOUTH NORWOOD PARTNERSHIP
17         202207                  DR EARNSHAW AND PARTNERS
18         202207                           MADEIRA MEDICAL
19         202207                   PROCARE HEALTH SERVICES
20         202207                      THE WOOTTONS SURGERY
21         202207                 THE STATHAM GROVE SURGERY
22         202207                    WESTERN AVENUE SURGERY
23         202207                          EASTBURY SURGERY
24         202207               KILBURN PARK MEDICAL CENTRE
25         202207               THE LONSDALE MEDICAL CENTRE
26         202207                   ALPERTON MEDICAL CENTRE
27         202207                         PARSONS GREEN WIC
28         202207                         PERRY TREE CENTRE
29         202207                 MARSTON FOREST HEALTHCARE
30         202207                           FIRECLAY HEALTH
31         202207                             ACORN SURGERY
32         202207               BEECH TREE MEDICAL PRACTICE
33         202207               STOCKINGFORD MEDICAL CENTRE
34         202207                      REETH MEDICAL CENTRE
35         202207                   EAST LANCASHIRE HOSPICE
36         202207                         THE BANKS SURGERY
37         202207                    DESFORD MEDICAL CENTRE
38         202207                        THE PATEL PRACTICE
39         202207                       DERMATOLOGY SERVICE
40         202207                   FOUNTAIN MEDICAL CENTRE
41         202207             COURT STREET MEDICAL PRACTICE
42         202207                                PEEL CROFT
43         202207                     PARK MEDICAL PRACTICE
44         202207                    RECOVERY STEPS CUMBRIA
45         202207                         RENACRES HOSPITAL
46         202207                 OXFORD HEALTH FT COMM NMP
47         202207                  BSUH DERMATOLOGY SERVICE
48         202207                MID DEVON MEDICAL PRACTICE
49         202207                      DEVON SQUARE SURGERY
50         202207                  HWLH DERMATOLOGY SERVICE
51         202207                         THE HEATH SURGERY
52         202207         COMMUNITY NON-MEDICAL PRESCRIBERS
53         202207           FORRESTER STREET MEDICAL CENTRE
54         202207                   DOG KENNEL LANE SURGERY
55         202207                    CONTINENCE SERVICE CGH
56         202207             FRANCES STREET MEDICAL CENTRE
57         202207           STREATHAM COMMON GROUP PRACTICE
58         202207                   BROMLEY COMMON PRACTICE
59         202207                WANDSWORTH COMMUNITY WARDS
60         202207               LINDLEY HOUSE HEALTH CENTRE
61         202207                  SIMPSON MEDICAL PRACTICE
62         202207                   AL-SHIFA MEDICAL CENTRE
63         202207                                 DR SANOMI
64         202207                      THE BROADWAY SURGERY
65         202207                     THE LYNDH

### E numa consulta simples de SQL retorno os prescribers adicionados no ultimo mês
- Lembrando que por se tratar apenas de uma amostra dos dados, temos o retorno apenas do **total dessa amostra**
- Aqui conto e seleciono os valor com **having count(PRACTICE_NAME) = 1** , pois o nome só se repetira 2x se estiver contido nos dois meses.
- **where YEAR_MONTH = 202208** não se torna necessario nesse caso, pois não tivemos prescribers no mes de julho que foram retirados no mês de agosto, pelo menos dentro dessa amostra.

In [79]:
df_add_no_mes_sql = spark.sql("""
SELECT PRACTICE_NAME as Prescribers, 
       count(PRACTICE_NAME) as Novo
FROM query_amostra
where YEAR_MONTH = 202208 -- Deixei comentado por poder ficar redundante a informação
group by PRACTICE_NAME
having count(PRACTICE_NAME) = 1
order by PRACTICE_NAME;
""")


#### Por ter encontrado problema como o 'case' na integração SQL > spark, optei por fazer apenas pelo spark.
- Aqui quis substituir a na linha o valor '1' por 'Sim'

In [80]:
df_add_no_mes_sql = df_add_no_mes_sql.withColumn("Novo", when(col("Novo") == "1","Sim")
      .otherwise("Nao"))

In [81]:
df_add_no_mes_sql.show()

+--------------------+----+
|         Prescribers|Novo|
+--------------------+----+
|(FRACTURE CLINIC)...| Sim|
|(IRLAM) SALFORD C...| Sim|
|       1 TO 1 CENTRE| Sim|
|1/MONTON MEDICAL ...| Sim|
|1/SALFORD MEDICAL...| Sim|
|      15 SEFTON ROAD| Sim|
|   168 MEDICAL GROUP| Sim|
|19 BEAUMONT STREE...| Sim|
|     240 WEXHAM ROAD| Sim|
|        27@NORTHGATE| Sim|
|        28@NORTHGATE| Sim|
|3/LOWER BROUGHTON...| Sim|
|3/SPRINGFIELD HOU...| Sim|
|301 EAST STREET S...| Sim|
|   3D MEDICAL CENTRE| Sim|
|    3VH RHEUMATOLOGY| Sim|
|           3W HEALTH| Sim|
|4 SEASONS MEDICAL...| Sim|
|         42 KINGSWAY| Sim|
|49 MARINE AVENUE ...| Sim|
+--------------------+----+
only showing top 20 rows



### Queria deixar mais apresentavel o resultado apenas com SQL, mas infelizmente o pyspark entrou em conflito por conta do 'case'
- Testei no **Google BigQuery** e funcionou normalmente.

In [83]:
'''df_add_no_mes_sql = spark.sql("""
SELECT PRACTICE_NAME as Prescribers,
       CASE
       WHEN count(PRACTICE_NAME) = 1 THEN 'sim'
       else 'Nao'
       end as Novo,
FROM query_amostra
group by Prescribers
having count(PRACTICE_NAME) = 1
order by 1;
""")'''

'df_add_no_mes_sql = spark.sql("""\nSELECT PRACTICE_NAME as Prescribers,\n       CASE\n       WHEN count(PRACTICE_NAME) = 1 THEN \'sim\'\n       else \'Nao\'\n       end as Novo,\nFROM query_amostra\ngroup by Prescribers\nhaving count(PRACTICE_NAME) = 1\norder by 1;\n""")'

### Exportando o resultado para um csv e conferindo a disponibilidade / armazenamento

In [84]:
df_add_no_mes_sql.toPandas().to_csv('Warehouse/Mes_08/df_add_no_mes_sql.csv', index=False)
df_add_no_mes_sql = pd.read_csv(r'Warehouse/Mes_08/df_add_no_mes_sql.csv')
df_add_no_mes_sql

Prescribers Novo
0                  (FRACTURE CLINIC) NORTH OOH  Sim
1     (IRLAM) SALFORD CARE CTRS MEDICAL PRACTI  Sim
2                                1 TO 1 CENTRE  Sim
3                    1/MONTON MEDICAL PRACTICE  Sim
4                   1/SALFORD MEDICAL PRACTICE  Sim
5                               15 SEFTON ROAD  Sim
6                            168 MEDICAL GROUP  Sim
7                   19 BEAUMONT STREET SURGERY  Sim
8                              240 WEXHAM ROAD  Sim
9                                 27@NORTHGATE  Sim
10                                28@NORTHGATE  Sim
11          3/LOWER BROUGHTON MEDICAL PRACTICE  Sim
12        3/SPRINGFIELD HOUSE MEDICAL PRACTICE  Sim
13                     301 EAST STREET SURGERY  Sim
14                           3D MEDICAL CENTRE  Sim
15                            3VH RHEUMATOLOGY  Sim
16                                   3W HEALTH  Sim
17                    4 SEASONS MEDICAL CENTRE  Sim
18                                 42 KINGSWAY  Sim
19                    49 MARINE AVENUE SURGERY  Sim
20              7 DAY ACCESS LITTLEBOROUGH HUB  Sim
21                   7 DAY ACCESS MIDDLETON HC  Sim
22                            7 DAY GP SERVICE  Sim
23                     8 TO 8 TOP-UP HUB ERITH  Sim
24                       8 TO 8 TOP-UP HUB QMH  Sim
25               A & E NON MEDICAL PRESCRIBERS  Sim
26                                     A&E GPS  Sim
27                            ABBAMOOR SURGERY  Sim
28                   ABBEY DALE MEDICAL CENTRE  Sim
29                  ABBEY FIELD MEDICAL CENTRE  Sim
30               ABBEY GRANGE MEDICAL PRACTICE  Sim
31                ABBEY HOUSE MEDICAL PRACTICE  Sim
32                   ABBEY MEADS MEDICAL PRACT  Sim
33                        ABBEY MEDICAL CENTRE  Sim
34                         ABBEY MEDICAL GROUP  Sim
35                      ABBEY MEDICAL PRACTICE  Sim
36                 ABBEY ROAD MEDICAL PRACTICE  Sim
37                          ABBEY ROAD SURGERY  Sim
38                               ABBEY SURGERY  Sim
39                          ABBEY WOOD SURGERY  Sim
40                   ABBEYSLADE PMS (DR CHAND)  Sim
41                           ABBEYVIEW SURGERY  Sim
42                           ABBEYWELL SURGERY  Sim
43                      ABBOTS BROMLEY SURGERY  Sim
44                   ABBOTSWOOD MEDICAL CENTRE  Sim
45                  ABBOTTSWOOD MEDICAL CENTRE  Sim
46                  ABERCROMBY FAMILY PRACTICE  Sim
47                          ABERFELDY PRACTICE  Sim
48                     ABERNETHY HOUSE SURGERY  Sim
49               ABH MANCHESTER & TRAFFORD CDS  Sim
50          ABINGDON FAMILY HEALTH CARE CENTRE  Sim
51                     ABINGTON MEDICAL CENTRE  Sim
52                       ABINGTON PARK SURGERY  Sim
53                            ABOUT HEALTH LTD  Sim
54                             ABRIDGE SURGERY  Sim
55                                      ACCT 2  Sim
56                                 ACE LTD OOH  Sim
57                                 ACHE CLINIC  Sim
58             ACHIEVE BOLTON RECOVERY SERVICE  Sim
59                       ACKLAM MEDICAL CENTRE  Sim
60                    ACLE MEDICAL PARTNERSHIP  Sim
61                 ACOCKS GREEN MEDICAL CENTRE  Sim
62                        ACORN MEDICAL CENTRE  Sim
63                      ACORN MEDICAL PRACTICE  Sim
64                              ACORN PRACTICE  Sim
65                               ACORN SURGERY  Sim
66                                ACRE SURGERY  Sim
67                           ACREFIELD SURGERY  Sim
68                      ACTIVE RECOVERY (CICS)  Sim
69                   ACTON LANE MEDICAL CENTRE  Sim
70                   ACTON TOWN MEDICAL CENTRE  Sim
71                   ACUTE GP REFERRAL SERVICE  Sim
72                    ACUTE MEDICAL UNIT (RBH)  Sim
73                         ACUTE MENTAL HEALTH  Sim
74                   ADAM HOUSE MEDICAL CENTRE  Sim
75             ADDACTION WIGAN & LEIGH (LEIGH)  Sim
76             ADDACTION WIGAN 

---
# Aqui finalizo o primeiro notebook com meu projeto do desafio!
#### Obrigado!